In [1]:
import numpy as np
%matplotlib inline
%matplotlib widget

import subprocess as sp
import os

from onset_detection import *
from onset_detection.audio import *
from onset_detection.od import *
from onset_detection.groovae import *

2023-12-11 17:07:52.580247: W tensorflow/core/platform/cloud/google_auth_provider.cc:184] All attempts to get a Google authentication bearer token failed, returning an empty token. Retrieving token from files failed with "NOT_FOUND: Could not locate the credentials file.". Retrieving token from GCE failed with "FAILED_PRECONDITION: Error executing an HTTP request: libcurl code 6 meaning 'Couldn't resolve host name', error details: Could not resolve host: metadata".
2023-12-11 17:07:57.814931: E tensorflow/stream_executor/cuda/cuda_driver.cc:271] failed call to cuInit: CUDA_ERROR_COMPAT_NOT_SUPPORTED_ON_DEVICE: forward compatibility was attempted on non supported HW
2023-12-11 17:07:57.814962: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:169] retrieving CUDA diagnostic information for host: turtleduck
2023-12-11 17:07:57.814967: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:176] hostname: turtleduck
2023-12-11 17:07:57.815113: I tensorflow/stream_executor/cuda/cuda_diag

INFO:tensorflow:Building MusicVAE model with BidirectionalLstmEncoder, GrooveLstmDecoder, and hparams:
{'max_seq_len': 32, 'z_size': 256, 'free_bits': 48, 'max_beta': 0.2, 'beta_rate': 0.0, 'batch_size': 1, 'grad_clip': 1.0, 'clip_mode': 'global_norm', 'grad_norm_clip_to_zero': 10000, 'learning_rate': 0.001, 'decay_rate': 0.9999, 'min_learning_rate': 1e-05, 'conditional': True, 'dec_rnn_size': [256, 256], 'enc_rnn_size': [512], 'dropout_keep_prob': 0.3, 'sampling_schedule': 'constant', 'sampling_rate': 0.0, 'use_cudnn': False, 'residual_encoder': False, 'residual_decoder': False, 'control_preprocessing_rnn_size': [256]}


INFO:tensorflow:Building MusicVAE model with BidirectionalLstmEncoder, GrooveLstmDecoder, and hparams:
{'max_seq_len': 32, 'z_size': 256, 'free_bits': 48, 'max_beta': 0.2, 'beta_rate': 0.0, 'batch_size': 1, 'grad_clip': 1.0, 'clip_mode': 'global_norm', 'grad_norm_clip_to_zero': 10000, 'learning_rate': 0.001, 'decay_rate': 0.9999, 'min_learning_rate': 1e-05, 'conditional': True, 'dec_rnn_size': [256, 256], 'enc_rnn_size': [512], 'dropout_keep_prob': 0.3, 'sampling_schedule': 'constant', 'sampling_rate': 0.0, 'use_cudnn': False, 'residual_encoder': False, 'residual_decoder': False, 'control_preprocessing_rnn_size': [256]}


INFO:tensorflow:
Encoder Cells (bidirectional):
  units: [512]



INFO:tensorflow:
Encoder Cells (bidirectional):
  units: [512]



...

Instructions for updating:
`scale_identity_multiplier` is deprecated; please combine it into `scale_diag` directly instead.


INFO:tensorflow:Unbundling checkpoint.


INFO:tensorflow:Unbundling checkpoint.


INFO:tensorflow:Restoring parameters from /tmp/tmpmkru2juq/groovae_2bar_tap_fixed_velocity/model.ckpt-3668


INFO:tensorflow:Restoring parameters from /tmp/tmpmkru2juq/groovae_2bar_tap_fixed_velocity/model.ckpt-3668
2023-12-11 17:08:12.407979: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:354] MLIR V1 optimization pass is not enabled


# Remixing
This jupyter notebook allows the remixing of manually tapped rhythms back into its original track, as well as trying out RAVE for style trasnfer and GrooVAE for Tap2Drums

### Pick a song
Choose a song you like from the list of songs below and listen back to it if you want:

- AC/DC - Back in Black:                        
song = `"ac_dc"`
- Amália - Barco Negro (Mão Preta):             
song = `"amália"`
- Amy Winehouse - Tears Dry On Their Own:       
song = `amy_whinehouse`
- Arctic Monkeys - The View From the Afternoon: 
song = `"arctic_monkeys"`
- The Beatles - Come Together:                  
song = `"beatles1"`
- The Beatles - In My Life:                     
song = `"beatles2"`
- Capitão Fausto - Morro na Praia:              
song = `"capitão_fausto"`
- David Miguel - INATEL:                        
song = `"david_miguel"`
- Gorillaz - Clint Eastwood:                    
song = `"gorillaz"`
- Ibeyi - River:                                
song = `"ibeyi"`
- Linda Martini - Febril (Tanto Mar):           
song = `"linda_martini"`
- Michael Jackson - Billie Jean:                
song = `"michael_jackson"`
- Queens of the Stone Age - No One Knows:       
song = `"qotsa"`
- Queen - Another One Bites the Dust:           
song = `"queen"`
- Slow J - Mundança:                            
song = `"slowj"`
- The Strokes - Reptilia:                       
song = `"strokes"`
- White Stripes - Seven Nation Army:            
song = `"white_stripes"`


In [2]:
#song = "ac_dc"
#song = "amália"
#song = "amy_winehouse"
#song = "arctic_monkeys"
#song = "beatles1"
#song = "beatles2"
##song = "capitão_fausto"
#song = "david_miguel"
#song = "gorillaz"
#song = "ibeyi"
#song = "linda_martini"
#song = "michael_jackson"
#song = "qotsa"
##song = "queen"
#song = "slowj"
song = "strokes"
#song = "white_stripes"

trim = True

song_path = song_dict[song]

trim_interval = None
# choose the interval in which you want to trim the audio (in seconds)
if trim:
    trim_interval = (115, 122)

song_audio, song_sr = read_audio(song_path, trim_interval)

### Separating the drums from the rest

Using S. Rouard et al.'s [Demucs](https://github.com/facebookresearch/demucs) [2], we can separate the drums from the rest of the other intruments:

In [3]:
output_dir = "../results/demucs"
song_path = song_dict[song]
song_name = song_path.split('/')[-1].split('.')[0]
drums_only = output_dir + "/mdx_extra_q/" + song_name + "/drums.wav"

separate = not os.path.exists(drums_only)

if separate:
    separate_drums = sp.run(["python3.9", "-m", "demucs", "--two-stems=drums", song_path, "-o", output_dir])

drums_audio, drums_sr = read_audio(drums_only, trim_interval)

In [4]:
# No drums
no_drums = output_dir + "/mdx_extra_q/" + song_name + "/no_drums.wav"
no_drums_audio, no_drums_sr = read_audio(no_drums, trim_interval)

### Tapped rhythms version
Listen back to tapped rhythms version of the track you picked

In [5]:
tapped_path = tapped_dict[song]
#tapped_path = "/home/asantos-6/Desktop/Record (online-voice-recorder.com).mp3"
#tapped_path = "/home/asantos-6/Downloads/Basic beatbox patterns for beginners Tutorial.mp3"

tapped_audio, tapped_sr = read_audio(tapped_path, trim_interval)

In [6]:
prep_path = prep_dict[song]
prepl_audio, prep_sr = read_audio(prep_path, trim_interval)

max_volume_dBFS=-100

prep_audio = limit_volume_np(prepl_audio)

## RAVE

In 2021, A. Caillon and P. Esling built [RAVE: Realtime Audio Variational autoEncoder](https://github.com/acids-ircam/RAVE) [3] which allows "both fast and high-quality audio waveform synthesis", but a byproduct of their system is that it is capable of doing Timbre Transfer between previously unseen audio sources and a target source on which the model was trained on.

Therefore, we can feed RAVE our tapped rhythm recordings and listen back to what RAVE outputs with its pre-trained darbouka model for example

### RAVE on Tapped Rhytms

In [7]:
#model = 'hi_hats_d7d5f0758c'
#model = 'woodblock-21_08_23'
#model = 'woodblock-28_08_23'
#model = 'woodblock-best-15_08_23'
#model = 'GMDrums_v3_22-09_96f9843578_streaming'
#model = 'darbouka'
model = 'GMDrums_v3_29-09_3M_streaming'

## Original tapped rhythms

In [10]:
rave_mixing(tapped_audio, tapped_path, tapped_sr, drums_audio, no_drums_audio, song_audio, no_drums_mixing=40)

tensor([[[ 0.0000, -0.5474,  0.4048,  ..., -0.1418, -1.3246,  0.4996],
         [ 0.0000,  0.0154,  0.0424,  ...,  0.5272, -1.1317, -0.2182],
         [ 0.0000,  0.1424,  0.1167,  ..., -0.2827,  0.4129, -0.4791],
         ...,
         [ 0.0000, -0.6242,  0.0271,  ...,  0.1790, -0.2083, -0.1568],
         [ 0.0000,  0.1010, -0.1267,  ..., -0.6292, -0.6252,  0.3905],
         [ 0.0000, -0.5508, -0.0024,  ...,  0.1672, -0.1505,  0.1289]]])
torch.Size([1, 16, 76])
Original song


Taps


RAVE output


Drum track


Reconstructed Drum track
tensor([[[ 0.0000, -0.3563,  0.4213,  ...,  0.2593,  3.7391, -2.1935],
         [ 0.0000, -0.0979, -2.6655,  ...,  3.1086, -0.4048, -2.1490],
         [ 0.0000, -2.4463,  1.5357,  ...,  0.2037,  0.8619, -0.2769],
         ...,
         [ 0.0000, -2.9180,  0.5884,  ...,  2.2707,  3.7224,  0.3022],
         [ 0.0000,  1.9995, -0.3302,  ..., -1.5061,  2.7817, -1.4393],
         [ 0.0000, -0.1887, -0.5185,  ...,  1.0407,  1.6795, -0.8173]]])
torch.Size([1, 16, 76])


...

Taps + RAVE


Remixing the taps onto the original song


Remixing RAVE's output onto the original song


Remixing RAVE's output onto the original track with drums


Remixing RAVE's reconstructed drums onto the original song


## Pre-processed tapped rhythms (Loudness & Normalization, Noise Reduction)

In [9]:
rave_mixing(prep_audio, prep_path, prep_sr, drums_audio, no_drums_audio, song_audio, no_drums_mixing=15)

tensor([[[ 0.0000, -1.4859,  1.8565,  ...,  0.2967, -1.5220,  0.1413],
         [ 0.0000, -1.0733,  0.0388,  ...,  1.2921, -2.7446,  0.4415],
         [ 0.0000,  0.0140,  0.5641,  ..., -0.4252,  0.0463,  0.4843],
         ...,
         [ 0.0000, -2.4202,  0.0088,  ...,  0.1551,  1.1564, -1.3619],
         [ 0.0000,  0.8641,  0.3723,  ..., -1.7832, -0.3936,  1.4703],
         [ 0.0000, -1.2253,  0.3971,  ...,  0.4335,  2.2198, -0.8250]]])
torch.Size([1, 16, 76])
Original song


Taps


RAVE output


Drum track


Reconstructed Drum track
tensor([[[ 0.0000, -0.3563,  0.4213,  ...,  0.2593,  3.7391, -2.1935],
         [ 0.0000, -0.0979, -2.6655,  ...,  3.1086, -0.4048, -2.1490],
         [ 0.0000, -2.4463,  1.5357,  ...,  0.2037,  0.8619, -0.2769],
         ...,
         [ 0.0000, -2.9180,  0.5884,  ...,  2.2707,  3.7224,  0.3022],
         [ 0.0000,  1.9995, -0.3302,  ..., -1.5061,  2.7817, -1.4393],
         [ 0.0000, -0.1887, -0.5185,  ...,  1.0407,  1.6795, -0.8173]]])
torch.Size([1, 16, 76])


...

Taps + RAVE


Remixing the taps onto the original song


Remixing RAVE's output onto the original song


Remixing RAVE's output onto the original track with drums


Remixing RAVE's reconstructed drums onto the original song
